# Adds a new column to the SF Crime and Trees files containing the zip code for that row, based on its latitude and longitude
----

In [1]:
# Sample URL format for pulling address by lat/lon
    # https://maps.googleapis.com/maps/api/geocode/json?latlng=40.714224,-73.961452&key=

In [2]:
# Dependencies
import json
import requests
import pandas as pd
import pprint as pp
from config import api_key
from config import maps_api_key

In [3]:
# Open SF Crime CSV
source_file = "Source CSVs/SF_Crime.csv"

# Pull the source file into a dataframe
sourceCrime = pd.read_csv(source_file)
sourceCrime

Unnamed: 0  Incident ID        Category  \
0                 0    180362289   VEHICLE THEFT   
1                 1    180360948    NON-CRIMINAL   
2                 2    180360879  OTHER OFFENSES   
3                 3    180360879  OTHER OFFENSES   
4                 4    180360879  OTHER OFFENSES   
...             ...          ...             ...   
2209994     2209995     30048199   DRUG/NARCOTIC   
2209995     2209996     30048199   DRUG/NARCOTIC   
2209996     2209997     30048199  OTHER OFFENSES   
2209997     2209998     30048183   LARCENY/THEFT   
2209998     2209999     30048456       VANDALISM   

                                       Description      Day        Date  \
0                                STOLEN MOTORCYCLE  Tuesday  2018-05-15   
1                     AIDED CASE, MENTAL DISTURBED  Tuesday  2018-05-15   
2                                 PAROLE VIOLATION  Tuesday  2018-05-15   
3                         TRAFFIC VIOLATION ARREST  Tuesday  2018-05-15   
4                                TRAFFIC VIOLATION  Tuesday  2018-05-15   
...                                            ...      ...         ...   
2209994                       POSSESSION OF HEROIN   Sunday  2003-01-12   
2209995      POSSESSION OF NARCOTICS PARAPHERNALIA   Sunday  2003-01-12   
2209996                           PAROLE VIOLATION   Sunday  2003-01-12   
2209997               PETTY THEFT FROM LOCKED AUTO   Sunday  2003-01-12   
2209998  MALICIOUS MISCHIEF, VANDALISM OF VEHICLES   Sunday  2003-01-12   

          Time  District   Longitude   Latitude  
0        10:30  SOUTHERN -122.411912  37.775207  
1        04:14  SOUTHERN -122.419258  37.775146  
2        02:01   MISSION -122.417813  37.757101  
3        02:01   MISSION -122.417813  37.757101  
4        02:01   MISSION -122.417813  37.757101  
...        ...       ...         ...        ...  
2209994  22:50  RICHMOND -122.466205  37.772541  
2209995  22:50  RICHMOND -122.466205  37.772541  
2209996  22:50  RICHMOND -122.466205  37.772541  
2209997  22:30   BAYVIEW -122.397202  37.753535  
2209998  22:30  SOUTHERN -122.421171  37.773643  

[2209999 rows x 10 columns]

# Drop unnecessary data to reduce file size before requesting from Geocode API
--------------------------------------------------------------------------

In [4]:
# Drop "Other" crimes
dropOther = sourceCrime[~sourceCrime.Category.str.contains("OTHER OFFENSES")]
dropOther

Unnamed: 0  Incident ID       Category  \
0                 0    180362289  VEHICLE THEFT   
1                 1    180360948   NON-CRIMINAL   
6                 6    180360835        ROBBERY   
7                 7    180360835  DRUG/NARCOTIC   
8                 8    180360794    LIQUOR LAWS   
...             ...          ...            ...   
2209993     2209994     30048202  DRUG/NARCOTIC   
2209994     2209995     30048199  DRUG/NARCOTIC   
2209995     2209996     30048199  DRUG/NARCOTIC   
2209997     2209998     30048183  LARCENY/THEFT   
2209998     2209999     30048456      VANDALISM   

                                       Description      Day        Date  \
0                                STOLEN MOTORCYCLE  Tuesday  2018-05-15   
1                     AIDED CASE, MENTAL DISTURBED  Tuesday  2018-05-15   
6                            ROBBERY, BODILY FORCE  Tuesday  2018-05-15   
7            POSSESSION OF NARCOTICS PARAPHERNALIA  Tuesday  2018-05-15   
8               MISCELLANEOUS LIQOUR LAW VIOLATION  Tuesday  2018-05-15   
...                                            ...      ...         ...   
2209993             POSSESSION OF METH-AMPHETAMINE   Sunday  2003-01-12   
2209994                       POSSESSION OF HEROIN   Sunday  2003-01-12   
2209995      POSSESSION OF NARCOTICS PARAPHERNALIA   Sunday  2003-01-12   
2209997               PETTY THEFT FROM LOCKED AUTO   Sunday  2003-01-12   
2209998  MALICIOUS MISCHIEF, VANDALISM OF VEHICLES   Sunday  2003-01-12   

          Time  District   Longitude   Latitude  
0        10:30  SOUTHERN -122.411912  37.775207  
1        04:14  SOUTHERN -122.419258  37.775146  
6        01:25  SOUTHERN -122.410042  37.781954  
7        01:25  SOUTHERN -122.410042  37.781954  
8        00:19      PARK -122.447761  37.769846  
...        ...       ...         ...        ...  
2209993  22:51   MISSION -122.426956  37.769247  
2209994  22:50  RICHMOND -122.466205  37.772541  
2209995  22:50  RICHMOND -122.466205  37.772541  
2209997  22:30   BAYVIEW -122.397202  37.753535  
2209998  22:30  SOUTHERN -122.421171  37.773643  

[1901442 rows x 10 columns]

In [5]:
# Drop "Missing Person" crimes
dropMissingPerson = dropOther[~dropOther.Category.str.contains("MISSING PERSON")]
dropMissingPerson

Unnamed: 0  Incident ID       Category  \
0                 0    180362289  VEHICLE THEFT   
1                 1    180360948   NON-CRIMINAL   
6                 6    180360835        ROBBERY   
7                 7    180360835  DRUG/NARCOTIC   
8                 8    180360794    LIQUOR LAWS   
...             ...          ...            ...   
2209993     2209994     30048202  DRUG/NARCOTIC   
2209994     2209995     30048199  DRUG/NARCOTIC   
2209995     2209996     30048199  DRUG/NARCOTIC   
2209997     2209998     30048183  LARCENY/THEFT   
2209998     2209999     30048456      VANDALISM   

                                       Description      Day        Date  \
0                                STOLEN MOTORCYCLE  Tuesday  2018-05-15   
1                     AIDED CASE, MENTAL DISTURBED  Tuesday  2018-05-15   
6                            ROBBERY, BODILY FORCE  Tuesday  2018-05-15   
7            POSSESSION OF NARCOTICS PARAPHERNALIA  Tuesday  2018-05-15   
8               MISCELLANEOUS LIQOUR LAW VIOLATION  Tuesday  2018-05-15   
...                                            ...      ...         ...   
2209993             POSSESSION OF METH-AMPHETAMINE   Sunday  2003-01-12   
2209994                       POSSESSION OF HEROIN   Sunday  2003-01-12   
2209995      POSSESSION OF NARCOTICS PARAPHERNALIA   Sunday  2003-01-12   
2209997               PETTY THEFT FROM LOCKED AUTO   Sunday  2003-01-12   
2209998  MALICIOUS MISCHIEF, VANDALISM OF VEHICLES   Sunday  2003-01-12   

          Time  District   Longitude   Latitude  
0        10:30  SOUTHERN -122.411912  37.775207  
1        04:14  SOUTHERN -122.419258  37.775146  
6        01:25  SOUTHERN -122.410042  37.781954  
7        01:25  SOUTHERN -122.410042  37.781954  
8        00:19      PARK -122.447761  37.769846  
...        ...       ...         ...        ...  
2209993  22:51   MISSION -122.426956  37.769247  
2209994  22:50  RICHMOND -122.466205  37.772541  
2209995  22:50  RICHMOND -122.466205  37.772541  
2209997  22:30   BAYVIEW -122.397202  37.753535  
2209998  22:30  SOUTHERN -122.421171  37.773643  

[1836622 rows x 10 columns]

In [6]:
# Drop "Non Criminal" crimes
dropNonCriminal = dropMissingPerson[~dropMissingPerson.Category.str.contains("NON-CRIMINAL")]
dropNonCriminal

Unnamed: 0  Incident ID       Category  \
0                 0    180362289  VEHICLE THEFT   
6                 6    180360835        ROBBERY   
7                 7    180360835  DRUG/NARCOTIC   
8                 8    180360794    LIQUOR LAWS   
9                 9    180360794       WARRANTS   
...             ...          ...            ...   
2209993     2209994     30048202  DRUG/NARCOTIC   
2209994     2209995     30048199  DRUG/NARCOTIC   
2209995     2209996     30048199  DRUG/NARCOTIC   
2209997     2209998     30048183  LARCENY/THEFT   
2209998     2209999     30048456      VANDALISM   

                                       Description      Day        Date  \
0                                STOLEN MOTORCYCLE  Tuesday  2018-05-15   
6                            ROBBERY, BODILY FORCE  Tuesday  2018-05-15   
7            POSSESSION OF NARCOTICS PARAPHERNALIA  Tuesday  2018-05-15   
8               MISCELLANEOUS LIQOUR LAW VIOLATION  Tuesday  2018-05-15   
9                  ENROUTE TO OUTSIDE JURISDICTION  Tuesday  2018-05-15   
...                                            ...      ...         ...   
2209993             POSSESSION OF METH-AMPHETAMINE   Sunday  2003-01-12   
2209994                       POSSESSION OF HEROIN   Sunday  2003-01-12   
2209995      POSSESSION OF NARCOTICS PARAPHERNALIA   Sunday  2003-01-12   
2209997               PETTY THEFT FROM LOCKED AUTO   Sunday  2003-01-12   
2209998  MALICIOUS MISCHIEF, VANDALISM OF VEHICLES   Sunday  2003-01-12   

          Time  District   Longitude   Latitude  
0        10:30  SOUTHERN -122.411912  37.775207  
6        01:25  SOUTHERN -122.410042  37.781954  
7        01:25  SOUTHERN -122.410042  37.781954  
8        00:19      PARK -122.447761  37.769846  
9        00:19      PARK -122.447761  37.769846  
...        ...       ...         ...        ...  
2209993  22:51   MISSION -122.426956  37.769247  
2209994  22:50  RICHMOND -122.466205  37.772541  
2209995  22:50  RICHMOND -122.466205  37.772541  
2209997  22:30   BAYVIEW -122.397202  37.753535  
2209998  22:30  SOUTHERN -122.421171  37.773643  

[1598715 rows x 10 columns]

In [7]:
# Drop "Secondary Codes" crimes
dropSecondary = dropNonCriminal[~dropNonCriminal.Category.str.contains("SECONDARY CODES")]
dropSecondary

Unnamed: 0  Incident ID       Category  \
0                 0    180362289  VEHICLE THEFT   
6                 6    180360835        ROBBERY   
7                 7    180360835  DRUG/NARCOTIC   
8                 8    180360794    LIQUOR LAWS   
9                 9    180360794       WARRANTS   
...             ...          ...            ...   
2209993     2209994     30048202  DRUG/NARCOTIC   
2209994     2209995     30048199  DRUG/NARCOTIC   
2209995     2209996     30048199  DRUG/NARCOTIC   
2209997     2209998     30048183  LARCENY/THEFT   
2209998     2209999     30048456      VANDALISM   

                                       Description      Day        Date  \
0                                STOLEN MOTORCYCLE  Tuesday  2018-05-15   
6                            ROBBERY, BODILY FORCE  Tuesday  2018-05-15   
7            POSSESSION OF NARCOTICS PARAPHERNALIA  Tuesday  2018-05-15   
8               MISCELLANEOUS LIQOUR LAW VIOLATION  Tuesday  2018-05-15   
9                  ENROUTE TO OUTSIDE JURISDICTION  Tuesday  2018-05-15   
...                                            ...      ...         ...   
2209993             POSSESSION OF METH-AMPHETAMINE   Sunday  2003-01-12   
2209994                       POSSESSION OF HEROIN   Sunday  2003-01-12   
2209995      POSSESSION OF NARCOTICS PARAPHERNALIA   Sunday  2003-01-12   
2209997               PETTY THEFT FROM LOCKED AUTO   Sunday  2003-01-12   
2209998  MALICIOUS MISCHIEF, VANDALISM OF VEHICLES   Sunday  2003-01-12   

          Time  District   Longitude   Latitude  
0        10:30  SOUTHERN -122.411912  37.775207  
6        01:25  SOUTHERN -122.410042  37.781954  
7        01:25  SOUTHERN -122.410042  37.781954  
8        00:19      PARK -122.447761  37.769846  
9        00:19      PARK -122.447761  37.769846  
...        ...       ...         ...        ...  
2209993  22:51   MISSION -122.426956  37.769247  
2209994  22:50  RICHMOND -122.466205  37.772541  
2209995  22:50  RICHMOND -122.466205  37.772541  
2209997  22:30   BAYVIEW -122.397202  37.753535  
2209998  22:30  SOUTHERN -122.421171  37.773643  

[1572930 rows x 10 columns]

In [8]:
# Drop the "Unnamed", "Time" and "District" columns
dropColumns = dropSecondary.drop(['Unnamed: 0', 'Time', 'District'], axis=1)
dropColumns

Incident ID       Category  \
0          180362289  VEHICLE THEFT   
6          180360835        ROBBERY   
7          180360835  DRUG/NARCOTIC   
8          180360794    LIQUOR LAWS   
9          180360794       WARRANTS   
...              ...            ...   
2209993     30048202  DRUG/NARCOTIC   
2209994     30048199  DRUG/NARCOTIC   
2209995     30048199  DRUG/NARCOTIC   
2209997     30048183  LARCENY/THEFT   
2209998     30048456      VANDALISM   

                                       Description      Day        Date  \
0                                STOLEN MOTORCYCLE  Tuesday  2018-05-15   
6                            ROBBERY, BODILY FORCE  Tuesday  2018-05-15   
7            POSSESSION OF NARCOTICS PARAPHERNALIA  Tuesday  2018-05-15   
8               MISCELLANEOUS LIQOUR LAW VIOLATION  Tuesday  2018-05-15   
9                  ENROUTE TO OUTSIDE JURISDICTION  Tuesday  2018-05-15   
...                                            ...      ...         ...   
2209993             POSSESSION OF METH-AMPHETAMINE   Sunday  2003-01-12   
2209994                       POSSESSION OF HEROIN   Sunday  2003-01-12   
2209995      POSSESSION OF NARCOTICS PARAPHERNALIA   Sunday  2003-01-12   
2209997               PETTY THEFT FROM LOCKED AUTO   Sunday  2003-01-12   
2209998  MALICIOUS MISCHIEF, VANDALISM OF VEHICLES   Sunday  2003-01-12   

          Longitude   Latitude  
0       -122.411912  37.775207  
6       -122.410042  37.781954  
7       -122.410042  37.781954  
8       -122.447761  37.769846  
9       -122.447761  37.769846  
...             ...        ...  
2209993 -122.426956  37.769247  
2209994 -122.466205  37.772541  
2209995 -122.466205  37.772541  
2209997 -122.397202  37.753535  
2209998 -122.421171  37.773643  

[1572930 rows x 7 columns]

In [9]:
cleaned_df = dropColumns

In [10]:
#Set the base URL
baseURL = "https://maps.googleapis.com/maps/api/geocode/json?latlng="

In [11]:
# Create the Zip Code column
cleaned_df['Zip Code'] = ""
cleaned_df

Incident ID       Category  \
0          180362289  VEHICLE THEFT   
6          180360835        ROBBERY   
7          180360835  DRUG/NARCOTIC   
8          180360794    LIQUOR LAWS   
9          180360794       WARRANTS   
...              ...            ...   
2209993     30048202  DRUG/NARCOTIC   
2209994     30048199  DRUG/NARCOTIC   
2209995     30048199  DRUG/NARCOTIC   
2209997     30048183  LARCENY/THEFT   
2209998     30048456      VANDALISM   

                                       Description      Day        Date  \
0                                STOLEN MOTORCYCLE  Tuesday  2018-05-15   
6                            ROBBERY, BODILY FORCE  Tuesday  2018-05-15   
7            POSSESSION OF NARCOTICS PARAPHERNALIA  Tuesday  2018-05-15   
8               MISCELLANEOUS LIQOUR LAW VIOLATION  Tuesday  2018-05-15   
9                  ENROUTE TO OUTSIDE JURISDICTION  Tuesday  2018-05-15   
...                                            ...      ...         ...   
2209993             POSSESSION OF METH-AMPHETAMINE   Sunday  2003-01-12   
2209994                       POSSESSION OF HEROIN   Sunday  2003-01-12   
2209995      POSSESSION OF NARCOTICS PARAPHERNALIA   Sunday  2003-01-12   
2209997               PETTY THEFT FROM LOCKED AUTO   Sunday  2003-01-12   
2209998  MALICIOUS MISCHIEF, VANDALISM OF VEHICLES   Sunday  2003-01-12   

          Longitude   Latitude Zip Code  
0       -122.411912  37.775207           
6       -122.410042  37.781954           
7       -122.410042  37.781954           
8       -122.447761  37.769846           
9       -122.447761  37.769846           
...             ...        ...      ...  
2209993 -122.426956  37.769247           
2209994 -122.466205  37.772541           
2209995 -122.466205  37.772541           
2209997 -122.397202  37.753535           
2209998 -122.421171  37.773643           

[1572930 rows x 8 columns]

In [12]:
# Store the DF length in a variable for printing progress
total = len(cleaned_df)
postcode = ""

In [ ]:
# Pull the address of each row's latitude and longitude from Google
for index, row in cleaned_df.iterrows():
    latitude = str(row['Latitude'])
    longitude = str(row['Longitude'])
    URL = baseURL + latitude + "," + longitude + "&key=" + maps_api_key
    
    # If statement to check whether this row has already had a postcode added
    if (row['Zip Code'] == "NaN") or (row['Zip Code'] == ""):
        # Try/except to handle error responses from API
        try:
            response = requests.get(URL).json()
            postcode = response['results'][0]['address_components'][7]['long_name']
            cleaned_df['Zip Code'] = postcode
            print(f"Processing row #{index} of {total}: {postcode}")
        except:
            cleaned_df['Zip Code'] = "NaN"
            print(f"Processing row #{index} of {total}: Bad Response")
    else:
        print(f"Processing row #{index} of {total}: Skipping.  Zip code already set")

Processing row #0 of 1572930: 94103
Processing row #6 of 1572930: 94103
Processing row #7 of 1572930: 94103
Processing row #8 of 1572930: 94117
Processing row #9 of 1572930: 94117
Processing row #10 of 1572930: 94110
Processing row #12 of 1572930: 94109
Processing row #13 of 1572930: Bad Response
Processing row #14 of 1572930: Bad Response
Processing row #15 of 1572930: 94103
Processing row #16 of 1572930: 94102
Processing row #17 of 1572930: 94103
Processing row #20 of 1572930: 94118
Processing row #21 of 1572930: 94114
Processing row #22 of 1572930: Bad Response
Processing row #23 of 1572930: Bad Response
Processing row #24 of 1572930: Bad Response
Processing row #26 of 1572930: 94110
Processing row #27 of 1572930: 94103
Processing row #28 of 1572930: 94158
Processing row #29 of 1572930: 94103
Processing row #30 of 1572930: 94103
Processing row #31 of 1572930: 94103
Processing row #34 of 1572930: 94107
Processing row #37 of 1572930: 94103
Processing row #38 of 1572930: 94103
Processi

Processing row #319 of 1572930: 94105
Processing row #321 of 1572930: 94109
Processing row #322 of 1572930: 94115
Processing row #323 of 1572930: 94103
Processing row #324 of 1572930: 94133
Processing row #325 of 1572930: 4902
Processing row #327 of 1572930: 94110
Processing row #328 of 1572930: 94132
Processing row #330 of 1572930: 94127
Processing row #331 of 1572930: 94127
Processing row #332 of 1572930: 94127
Processing row #333 of 1572930: 94127
Processing row #334 of 1572930: 94102
Processing row #336 of 1572930: 94134
Processing row #337 of 1572930: 94109
Processing row #339 of 1572930: 94110
Processing row #340 of 1572930: 94110
Processing row #341 of 1572930: 94110
Processing row #342 of 1572930: 94115
Processing row #343 of 1572930: 94107
Processing row #345 of 1572930: 94112
Processing row #346 of 1572930: 94102
Processing row #347 of 1572930: 94133
Processing row #348 of 1572930: 94133
Processing row #349 of 1572930: 94133
Processing row #350 of 1572930: 94115
Processing ro

Processing row #623 of 1572930: 94117
Processing row #624 of 1572930: 94108
Processing row #625 of 1572930: 94134
Processing row #626 of 1572930: 94105
Processing row #627 of 1572930: 94110
Processing row #628 of 1572930: 94109
Processing row #630 of 1572930: 94111
Processing row #633 of 1572930: Bad Response
Processing row #634 of 1572930: 94114
Processing row #635 of 1572930: 94102
Processing row #636 of 1572930: Bad Response
Processing row #637 of 1572930: 94114
Processing row #638 of 1572930: 94114
Processing row #639 of 1572930: 94121
Processing row #640 of 1572930: 94121
Processing row #641 of 1572930: 94115
Processing row #642 of 1572930: 94115
Processing row #646 of 1572930: 94103
Processing row #648 of 1572930: 94103
Processing row #649 of 1572930: Bad Response
Processing row #651 of 1572930: 94111
Processing row #652 of 1572930: 94111
Processing row #653 of 1572930: 94111
Processing row #654 of 1572930: 94102
Processing row #655 of 1572930: Bad Response
Processing row #658 of

Processing row #935 of 1572930: 94112
Processing row #936 of 1572930: 94103
Processing row #938 of 1572930: 94123
Processing row #939 of 1572930: 94123
Processing row #940 of 1572930: 94108
Processing row #941 of 1572930: United States
Processing row #942 of 1572930: 94114
Processing row #943 of 1572930: 94110
Processing row #946 of 1572930: 94133
Processing row #947 of 1572930: 94132
Processing row #948 of 1572930: 94103
Processing row #949 of 1572930: 94103
Processing row #950 of 1572930: 94102
Processing row #951 of 1572930: 94102
Processing row #953 of 1572930: 94103
Processing row #954 of 1572930: 94114
Processing row #955 of 1572930: 94114
Processing row #956 of 1572930: 94122
Processing row #959 of 1572930: 94102
Processing row #960 of 1572930: 94115
Processing row #961 of 1572930: 94115
Processing row #962 of 1572930: 94111
Processing row #963 of 1572930: Bad Response
Processing row #964 of 1572930: 94133
Processing row #965 of 1572930: Bad Response
Processing row #966 of 15729

Processing row #1231 of 1572930: 94112
Processing row #1232 of 1572930: 94123
Processing row #1233 of 1572930: 94103
Processing row #1234 of 1572930: 94107
Processing row #1235 of 1572930: 94110
Processing row #1236 of 1572930: 94122
Processing row #1237 of 1572930: 94122
Processing row #1238 of 1572930: 94105
Processing row #1239 of 1572930: Bad Response
Processing row #1240 of 1572930: 94118
Processing row #1243 of 1572930: United States
Processing row #1244 of 1572930: Bad Response
Processing row #1245 of 1572930: 94105
Processing row #1246 of 1572930: 94110
Processing row #1248 of 1572930: 94110
Processing row #1249 of 1572930: 94122
Processing row #1252 of 1572930: 94118
Processing row #1253 of 1572930: 94103
Processing row #1254 of 1572930: 94111
Processing row #1255 of 1572930: 94133
Processing row #1256 of 1572930: 94114
Processing row #1257 of 1572930: 94102
Processing row #1260 of 1572930: 94109
Processing row #1262 of 1572930: 94102
Processing row #1263 of 1572930: 94103
Pro

...

Processing row #187890 of 1572930: Bad Response
Processing row #187891 of 1572930: Bad Response
Processing row #187892 of 1572930: Bad Response
Processing row #187893 of 1572930: Bad Response
Processing row #187895 of 1572930: Bad Response
Processing row #187896 of 1572930: Bad Response
Processing row #187897 of 1572930: Bad Response
Processing row #187898 of 1572930: Bad Response
Processing row #187899 of 1572930: Bad Response
Processing row #187901 of 1572930: Bad Response
Processing row #187904 of 1572930: Bad Response
Processing row #187905 of 1572930: Bad Response
Processing row #187907 of 1572930: Bad Response
Processing row #187908 of 1572930: Bad Response
Processing row #187909 of 1572930: Bad Response
Processing row #187910 of 1572930: Bad Response
Processing row #187911 of 1572930: Bad Response
Processing row #187912 of 1572930: Bad Response
Processing row #187913 of 1572930: Bad Response
Processing row #187914 of 1572930: Bad Response
Processing row #187915 of 1572930: Bad R

From cffi callback <function _verify_callback at 0x000001EF49AD78C8>:
Traceback (most recent call last):
  File "C:\Users\mahlo\.conda\envs\PythonData\lib\site-packages\OpenSSL\SSL.py", line 306, in wrapper
    @wraps(callback)
KeyboardInterrupt


Processing row #188070 of 1572930: Bad Response
Processing row #188071 of 1572930: Bad Response
Processing row #188072 of 1572930: Bad Response
Processing row #188075 of 1572930: Bad Response
Processing row #188076 of 1572930: Bad Response
Processing row #188077 of 1572930: Bad Response
Processing row #188078 of 1572930: Bad Response
Processing row #188079 of 1572930: Bad Response
Processing row #188080 of 1572930: Bad Response
Processing row #188082 of 1572930: Bad Response
Processing row #188083 of 1572930: Bad Response
Processing row #188087 of 1572930: Bad Response
Processing row #188089 of 1572930: Bad Response
Processing row #188091 of 1572930: Bad Response
Processing row #188093 of 1572930: Bad Response
Processing row #188094 of 1572930: Bad Response
Processing row #188097 of 1572930: Bad Response
Processing row #188100 of 1572930: Bad Response
Processing row #188103 of 1572930: Bad Response
Processing row #188104 of 1572930: Bad Response
Processing row #188105 of 1572930: Bad R

Processing row #188353 of 1572930: Bad Response
Processing row #188355 of 1572930: Bad Response
Processing row #188356 of 1572930: Bad Response
Processing row #188357 of 1572930: Bad Response
Processing row #188358 of 1572930: Bad Response
Processing row #188359 of 1572930: Bad Response
Processing row #188362 of 1572930: Bad Response
Processing row #188365 of 1572930: Bad Response
Processing row #188366 of 1572930: Bad Response
Processing row #188367 of 1572930: Bad Response
Processing row #188368 of 1572930: Bad Response
Processing row #188372 of 1572930: Bad Response
Processing row #188373 of 1572930: Bad Response
Processing row #188375 of 1572930: Bad Response
Processing row #188376 of 1572930: Bad Response
Processing row #188379 of 1572930: Bad Response
Processing row #188381 of 1572930: Bad Response
Processing row #188382 of 1572930: Bad Response
Processing row #188383 of 1572930: Bad Response
Processing row #188384 of 1572930: Bad Response
Processing row #188385 of 1572930: Bad R

Processing row #188571 of 1572930: Bad Response
Processing row #188574 of 1572930: Bad Response
Processing row #188575 of 1572930: Bad Response
Processing row #188577 of 1572930: Bad Response
Processing row #188582 of 1572930: Bad Response
Processing row #188583 of 1572930: Bad Response
Processing row #188584 of 1572930: Bad Response
Processing row #188585 of 1572930: Bad Response
Processing row #188586 of 1572930: Bad Response
Processing row #188588 of 1572930: Bad Response
Processing row #188589 of 1572930: Bad Response
Processing row #188590 of 1572930: Bad Response
Processing row #188591 of 1572930: Bad Response
Processing row #188592 of 1572930: Bad Response
Processing row #188593 of 1572930: Bad Response
Processing row #188594 of 1572930: Bad Response
Processing row #188595 of 1572930: Bad Response
Processing row #188596 of 1572930: Bad Response
Processing row #188597 of 1572930: Bad Response
Processing row #188599 of 1572930: Bad Response
Processing row #188600 of 1572930: Bad R

In [ ]:
cleaned_df.to_csv("Source CSVs/SF_Crime_with_zips.csv")
print("Export complete")

In [ ]:
print("test")